In [ ]:
# pip install basemap


In [1]:
import os
import sys
import pandas as pd
import numpy as np
import obspy
from tqdm import tqdm

from obspy.clients.fdsn import Client
from obspy.clients.fdsn import Client as FDSNClient

from mpl_toolkits.basemap import Basemap


from pnwstore.mseed import WaveformClient
from datetime import datetime
from matplotlib import pyplot as plt
from matplotlib.backends.backend_pdf import PdfPages

from obspy import UTCDateTime

from tqdm import tqdm
from obspy.geodetics import locations2degrees, degrees2kilometers

notebook_dir = os.getcwd()
parent_dir = os.path.abspath(os.path.join(notebook_dir, '../'))
if parent_dir not in sys.path:
    sys.path.append(parent_dir)
    
from plot_utils import *
from qc_utils import * 

## Morton Catalog

In [2]:
# Read Morton's catalog
events_morton = pd.read_csv('../data/ds01.csv')
# Convert the TSTRING to datetime
events_morton['datetime'] = pd.to_datetime(events_morton['TSTRING'], format='%Y%m%d%H%M%S', utc=True)
# Get the events in the Morton catalog 
t1 = pd.Timestamp('2011-1-1 00:00:00.000000+0000', tz='UTC')
t2 = pd.Timestamp('2015-12-31 23:59:59.999999+0000', tz='UTC')

events_morton= events_morton.loc[(events_morton['datetime'] > t1) & (events_morton['datetime'] < t2) ]

events_morton.head()

CI YEAR       TSTRING    YEAR  MONTH   DAY  HOUR  MINUTE  SECOND      LAT  \
0      1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    7.37  47.3217   
1      1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    7.72  44.2888   
2      1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    8.56  44.3017   
3      1.0  2.011073e+13  2011.0    7.0  26.0   7.0    31.0    2.17  48.2635   
4      1.0  2.011073e+13  2011.0    7.0  26.0   9.0    50.0   27.63  48.3032   

        LON  ...  dist to nearest stn  tt RMS   ERH   ERZ  STRIKE  DIP  RAKE  \
0 -123.2708  ...                 27.4    0.19   0.8   1.2     NaN  NaN   NaN   
1 -124.3340  ...                163.8    0.06  13.1   3.2     NaN  NaN   NaN   
2 -124.3180  ...                131.1    0.50  35.4  22.2     NaN  NaN   NaN   
3 -124.9298  ...                 44.4    0.77   3.5   6.4     NaN  NaN   NaN   
4 -124.9157  ...                 46.1    0.94   4.0   6.9     NaN  NaN   NaN   

   PLATE DESIGNATION  TEMPLATE EVENT?                  datetime  
0          Interface          Catalog 2011-07-26 01:02:07+00:00  
1        Upper Plate              NaN 2011-07-26 01:02:07+00:00  
2        Upper Plate              NaN 2011-07-26 01:02:08+00:00  
3        Upper Plate              NaN 2011-07-26 07:31:02+00:00  
4        Upper Plate                T 2011-07-26 09:50:27+00:00  

[5 rows x 24 columns]

In [3]:
events_morton

CI YEAR       TSTRING    YEAR  MONTH   DAY  HOUR  MINUTE  SECOND  \
0         1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    7.37   
1         1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    7.72   
2         1.0  2.011073e+13  2011.0    7.0  26.0   1.0     2.0    8.56   
3         1.0  2.011073e+13  2011.0    7.0  26.0   7.0    31.0    2.17   
4         1.0  2.011073e+13  2011.0    7.0  26.0   9.0    50.0   27.63   
...       ...           ...     ...    ...   ...   ...     ...     ...   
5277      4.0  2.015101e+13  2015.0   10.0   7.0   8.0     1.0   50.83   
5278      4.0  2.015101e+13  2015.0   10.0   7.0   8.0     7.0    8.40   
5279      4.0  2.015101e+13  2015.0   10.0   7.0  11.0    31.0   26.69   
5280      4.0  2.015101e+13  2015.0   10.0   7.0  18.0    11.0    9.52   
5281      4.0  2.015101e+13  2015.0   10.0   7.0  21.0    45.0   50.37   

          LAT       LON  ...  dist to nearest stn  tt RMS   ERH   ERZ  STRIKE  \
0     47.3217 -123.2708  ...                 27.4    0.19   0.8   1.2     NaN   
1     44.2888 -124.3340  ...                163.8    0.06  13.1   3.2     NaN   
2     44.3017 -124.3180  ...                131.1    0.50  35.4  22.2     NaN   
3     48.2635 -124.9298  ...                 44.4    0.77   3.5   6.4     NaN   
4     48.3032 -124.9157  ...                 46.1    0.94   4.0   6.9     NaN   
...       ...       ...  ...                  ...     ...   ...   ...     ...   
5277  40.5895 -124.0455  ...                  5.4    0.14   0.9   0.8     NaN   
5278  40.5380 -123.7217  ...                 14.9    0.09   3.3  13.5     NaN   
5279  40.5822 -124.0432  ...                  5.6    0.05   1.7   0.8     NaN   
5280  40.2710 -124.3777  ...                  7.9    0.19   0.7   0.2     NaN   
5281  40.1602 -123.8320  ...                 29.4    0.22   1.3  18.6     NaN   

      DIP  RAKE  PLATE DESIGNATION  TEMPLATE EVENT?                  datetime  
0     NaN   NaN          Interface          Catalog 2011-07-26 01:02:07+00:00  
1     NaN   NaN        Upper Plate              NaN 2011-07-26 01:02:07+00:00  
2     NaN   NaN        Upper Plate              NaN 2011-07-26 01:02:08+00:00  
3     NaN   NaN        Upper Plate              NaN 2011-07-26 07:31:02+00:00  
4     NaN   NaN        Upper Plate                T 2011-07-26 09:50:27+00:00  
...   ...   ...                ...              ...                       ...  
5277  NaN   NaN               Slab              NaN 2015-10-07 08:01:50+00:00  
5278  NaN   NaN        Upper Plate              NaN 2015-10-07 08:07:08+00:00  
5279  NaN   NaN               Slab              NaN 2015-10-07 11:31:26+00:00  
5280  NaN   NaN        Upper Plate              NaN 2015-10-07 18:11:09+00:00  
5281  NaN   NaN              Undef              NaN 2015-10-07 21:45:50+00:00  

[5282 rows x 24 columns]

## ANSS Catalog

In [4]:
events_anss = pd.read_csv('../data/datasets_anss/anss_2011-15.csv')
events_anss['datetime'] = pd.to_datetime(events_anss['time'], format='%Y-%m-%dT%H:%M:%S.%fZ', utc=True)
events_anss= events_anss.loc[(events_anss['datetime'] > t1) & (events_anss['datetime'] < t2) ]
events_anss

Unnamed: 0                      time   latitude   longitude   depth  \
0                0  2011-01-01T00:21:06.570Z  38.809834 -122.793663   1.746   
1                1  2011-01-01T02:04:41.480Z  38.789001 -122.747002  -0.844   
2                2  2011-01-01T02:53:49.640Z  38.817333 -122.821167   1.929   
3                3  2011-01-01T03:11:04.720Z  38.841835 -122.829002   1.076   
4                4  2011-01-01T03:32:55.630Z  38.835833 -122.807000   0.947   
...            ...                       ...        ...         ...     ...   
131527      131527  2015-12-31T22:15:46.650Z  38.837502 -122.825333   1.450   
131528      131528  2015-12-31T22:18:13.120Z  41.856400 -119.599200   8.700   
131529      131529  2015-12-31T23:19:21.650Z  38.823334 -122.765663   1.680   
131530      131530  2015-12-31T23:22:20.730Z  38.841000 -122.878166   1.730   
131531      131531  2015-12-31T23:53:17.350Z  40.457667 -124.763000  24.960   

         mag magType   nst    gap      dmin  ...  \
0       0.88      md  14.0   73.0  0.001802  ...   
1       0.28      md   5.0  122.0  0.009910  ...   
2       1.03      md  40.0   44.0  0.010810  ...   
3       0.43      md   7.0   77.0  0.013510  ...   
4       0.16      md   9.0  112.0  0.012610  ...   
...      ...     ...   ...    ...       ...  ...   
131527  0.18      md   6.0  180.0  0.008108  ...   
131528  1.40      ml   6.0  210.1  0.175000  ...   
131529  0.54      md   7.0   99.0  0.008108  ...   
131530  0.77      md   8.0   95.0  0.007207  ...   
131531  2.32      md  16.0  301.0  0.325200  ...   

                                      place        type horizontalError  \
0              6 km WSW of Cobb, California  earthquake            0.30   
1              4 km SSW of Cobb, California  earthquake            0.42   
2                8 km W of Cobb, California  earthquake            0.14   
3              9 km WNW of Cobb, California  earthquake            0.43   
4              7 km WNW of Cobb, California  earthquake            0.33   
...                                     ...         ...             ...   
131527           9 km W of Cobb, California  earthquake            0.66   
131528  45 km E of Fort Bidwell, California  earthquake             NaN   
131529           3 km W of Cobb, California  earthquake            0.50   
131530  12 km ENE of Cloverdale, California  earthquake            0.58   
131531    44 km WSW of Ferndale, California  earthquake            0.99   

       depthError magError magNst     status  locationSource  magSource  \
0            0.56    0.010   16.0  automatic              nc         nc   
1            2.39    0.200    6.0  automatic              nc         nc   
2            0.19    0.060   13.0   reviewed              nc         nc   
3            0.88    0.150    7.0  automatic              nc         nc   
4            0.72    0.123    2.0   reviewed              nc         nc   
...           ...      ...    ...        ...             ...        ...   
131527       1.08    0.110    2.0  automatic              nc         nc   
131528       3.40    0.210    3.0   reviewed              nn         nn   
131529       1.54    0.030    2.0  automatic              nc         nc   
131530       1.02    0.180    3.0  automatic              nc         nc   
131531       4.72    0.324   18.0   reviewed              nc         nc   

                               datetime  
0      2011-01-01 00:21:06.570000+00:00  
1      2011-01-01 02:04:41.480000+00:00  
2      2011-01-01 02:53:49.640000+00:00  
3      2011-01-01 03:11:04.720000+00:00  
4      2011-01-01 03:32:55.630000+00:00  
...                                 ...  
131527 2015-12-31 22:15:46.650000+00:00  
131528 2015-12-31 22:18:13.120000+00:00  
131529 2015-12-31 23:19:21.650000+00:00  
131530 2015-12-31 23:22:20.730000+00:00  
131531 2015-12-31 23:53:17.350000+00:00  

[131532 rows x 24 columns]

## Our Catalog

In [5]:
# Load all the pick assignments 
mycatalog_picks = pd.read_csv('../data/datasets_pnsn_jdf/all_pick_assignments_pnsn_jdf.csv')
mycatalog = mycatalog_picks.drop_duplicates(subset=['idx'])
# Convert the time series in all_pick_assignments to datetime
mycatalog['datetime'] = pd.to_datetime(mycatalog['time'], utc = True)
mycatalog=mycatalog.loc[(mycatalog['datetime'] > t1) & (mycatalog['datetime'] < t2) ]
mycatalog

/tmp/ipykernel_2254968/766234642.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mycatalog['datetime'] = pd.to_datetime(mycatalog['time'], utc = True)


Unnamed: 0    idx                              time           x  \
0                0      2  2011-12-10 22:44:46.018805+00:00  -96.503032   
6                6      3  2011-12-26 18:06:15.493905+00:00  -36.258365   
12              12      8  2012-02-04 20:05:31.130689+00:00 -203.604662   
19              19      9  2012-02-06 08:17:12.331083+00:00  -71.958908   
25              25     16  2012-03-18 18:48:43.937964+00:00  185.754391   
...            ...    ...                               ...         ...   
173759      173759  30603  2015-09-14 05:33:02.229963+00:00  -60.802488   
173769      173769  30604  2015-09-14 06:09:08.238133+00:00 -145.591279   
173779      173779  30605  2015-09-14 13:34:01.138138+00:00 -161.210267   
173788      173788  30609  2015-09-15 09:12:54.234894+00:00 -142.244353   
173794      173794  30610  2015-09-15 17:31:03.266140+00:00   71.958908   

                 y          z  picks   latitude   longitude      depth  \
0        58.401356  12.890625      6  45.018973 -126.724334  12.890625   
6       132.782258  41.015625      6  45.693849 -125.965511  41.015625   
12      483.230738  49.609375      7  48.813643 -128.272371  49.609375   
19     -123.259693   1.171875      6  43.387215 -126.388083   1.171875   
25      252.936022  25.390625      8  46.749918 -123.068939  25.390625   
...            ...        ...    ...        ...         ...        ...   
173759 -370.719232   0.390625     10  41.160599 -126.224435   0.390625   
173769 -447.960938  49.609375     10  40.454578 -127.216333  49.609375   
173779 -435.087320  49.609375      9  40.567566 -127.403644  49.609375   
173788 -277.743104  16.015625      6  41.987174 -127.216502  16.015625   
173794 -465.125761  47.265625      6  40.309645 -124.653498  47.265625   

        event_idx  pick_idx  residual station phase     time_pick  \
0               2   1655834  0.530519    J35A     P  1.323557e+09   
6               3   1654163 -0.561964    J35A     P  1.324923e+09   
12              8    345847 -1.158387    J35A     P  1.328386e+09   
19              9    121103 -0.167694    J35A     P  1.328516e+09   
25             16    129536 -0.081932    J35A     P  1.332097e+09   
...           ...       ...       ...     ...   ...           ...   
173759      30603   1476568  0.078527    G10D     P  1.442209e+09   
173769      30604   1476574 -0.531605    G10D     P  1.442211e+09   
173779      30605   1476584  0.303990    G10D     P  1.442238e+09   
173788      30609   1452051 -0.035427    G10D     P  1.442308e+09   
173794      30610   1452085  0.084264    G10D     P  1.442338e+09   

                               datetime  
0      2011-12-10 22:44:46.018805+00:00  
6      2011-12-26 18:06:15.493905+00:00  
12     2012-02-04 20:05:31.130689+00:00  
19     2012-02-06 08:17:12.331083+00:00  
25     2012-03-18 18:48:43.937964+00:00  
...                                 ...  
173759 2015-09-14 05:33:02.229963+00:00  
173769 2015-09-14 06:09:08.238133+00:00  
173779 2015-09-14 13:34:01.138138+00:00  
173788 2015-09-15 09:12:54.234894+00:00  
173794 2015-09-15 17:31:03.266140+00:00  

[18868 rows x 17 columns]

## Run this loop

In [7]:
matched_events_mycatalog2morton = []
matched_times_morton2mycatalog = []
matched_events_morton2mycatalog = []
unmatched_times_morton2mycatalog = []
unmatched_events_morton2mycatalog = []
unmatched_events_mycatalog2morton_and_anss = []
matched_events_anss2mycatalog=[]
matched_events_mycatalog2anss = []
unmatched_times_anss2mycatalog = []
unmatched_events_anss2mycatalog = []
matched_times_anss2mycatalog =[]

time_threshold = 5 # in seconds
dist_threshold =25

lat_morton2mycatalog = []
lon_morton2mycatalog = []

lat_anss2mycatalog =[]
lon_anss2mycatalog = []

# A set to keep track of matched indices in mycatalog
matched_indices_morton = set()
matched_indices_anss = set()
count_c = 0
count_d = 0
# Loop over events in Morton's catalog
for i in range(len(events_morton)):
    t11 = events_morton.iloc[i]['datetime']
    olat = events_morton.iloc[i]['LAT']
    olon = events_morton.iloc[i]['LON']
    
                                       
    condition = (mycatalog['datetime'] >= t11 - pd.Timedelta(seconds=time_threshold)) & \
                     (mycatalog['datetime'] <= t11 + pd.Timedelta(seconds=time_threshold)) & \
                     (degrees2kilometers(locations2degrees(olat, olon, mycatalog['latitude'], mycatalog['longitude'])) <= dist_threshold)                        
    matched_df = mycatalog.loc[condition]

    if len(matched_df) == 1:
        print('matched idx of Morton: ',i)
        count_c+=1
        matched_times_morton2mycatalog.append(t11)
        matched_events_morton2mycatalog.append(events_morton.iloc[i])
        lat_morton2mycatalog.append(events_morton.iloc[i]['LAT'])
        lon_morton2mycatalog.append(events_morton.iloc[i]['LON'])
        matched_events_mycatalog2morton.append(matched_df)
        matched_indices_morton.update(matched_df['idx'])
    elif len(matched_df) > 1:
        print('matched idx of Morton: ',i)

        count_d+=1
        diffs = abs(matched_df['datetime'] - t11)
        closest_index = diffs.idxmin()
        closest_event = matched_df.loc[[closest_index]]
        matched_times_morton2mycatalog.append(t11)
        matched_events_morton2mycatalog.append(events_morton.iloc[i])
        lat_morton2mycatalog.append(events_morton.iloc[i]['LAT'])
        lon_morton2mycatalog.append(events_morton.iloc[i]['LON'])
        matched_events_mycatalog2morton.append(closest_event)
        matched_indices_morton.update(closest_event['idx'])
    else:
        unmatched_times_morton2mycatalog.append(t11)
        unmatched_events_morton2mycatalog.append(events_morton.iloc[i])

# All events in mycatalog not matched with Morton's catalog are unmatched
unmatched_indices_morton = set(mycatalog.idx) - matched_indices_morton
# unmatched_events_mycatalog2morton = mycatalog.iloc[list(unmatched_indices_morton)]
count_a =0
count_b =0
# Loop over events in ANSS catalog
for i in range(len(events_anss)):
    t11 = events_anss.iloc[i]['datetime']
    olat = events_anss.iloc[i]['latitude']
    olon = events_anss.iloc[i]['longitude']
    
                                       
    condition = (mycatalog['datetime'] >= t11 - pd.Timedelta(seconds=time_threshold)) & \
                     (mycatalog['datetime'] <= t11 + pd.Timedelta(seconds=time_threshold)) & \
                     (degrees2kilometers(locations2degrees(olat, olon, mycatalog['latitude'], mycatalog['longitude'])) <= dist_threshold)                        
    matched_df = mycatalog.loc[condition]
    
    if len(matched_df) == 1:
        
        count_a+=1
        matched_times_anss2mycatalog.append(t11)
        matched_events_anss2mycatalog.append(events_anss.iloc[i])
        lat_anss2mycatalog.append(events_anss.iloc[i]['latitude'])
        lon_anss2mycatalog.append(events_anss.iloc[i]['longitude'])
        matched_events_mycatalog2anss.append(matched_df)
        matched_indices_anss.update(matched_df['idx'])
        
    elif len(matched_df) > 1:
        count_b+=1
        diffs = abs(matched_df['datetime'] - t11)
        closest_index = diffs.idxmin()
        closest_event = matched_df.loc[[closest_index]]
        matched_times_anss2mycatalog.append(t11)
        matched_events_anss2mycatalog.append(events_anss.iloc[i])
        lat_anss2mycatalog.append(events_anss.iloc[i]['latitude'])
        lon_anss2mycatalog.append(events_anss.iloc[i]['longitude'])
        matched_events_mycatalog2anss.append(closest_event)
        matched_indices_anss.update(closest_event['idx'])
        
    else:
        unmatched_times_anss2mycatalog.append(t11)
        unmatched_events_anss2mycatalog.append(events_anss.iloc[i])

# All events in mycatalog not matched with ANSS catalog are unmatched
unmatched_indices_anss = set(mycatalog.idx) - matched_indices_anss

unmatched_indices_morton_and_anss = unmatched_indices_morton.intersection(unmatched_indices_anss)
print(len(mycatalog),len(unmatched_indices_morton_and_anss))

# unmatched_events_mycatalog2morton_and_anss = mycatalog.iloc[list(unmatched_indices_morton_and_anss)]
unmatched_events_mycatalog2morton_and_anss = mycatalog.loc[mycatalog['event_idx'].isin(list(unmatched_indices_morton_and_anss))]


print(f"length of mycatalog:{len(mycatalog)}")
print(f"length of events_morton:{len(events_morton)}")
print(f"length of events_anss:{len(events_anss)}")
print(f"matched_indices_morton:{len(matched_indices_morton)}")
print(f"matched_indices_anss:{len(matched_indices_anss)}")
print(f"unmatched_indices_morton:{len(unmatched_indices_morton)}")
print(f"unmatched_indices_anss:{len(unmatched_indices_anss)}")
print(f"unmatched_indices_morton_and_anss (new events):{len(unmatched_indices_morton_and_anss)}")


matched idx of Morton:  284
matched idx of Morton:  499
matched idx of Morton:  504
matched idx of Morton:  510
matched idx of Morton:  511
matched idx of Morton:  512
matched idx of Morton:  513
matched idx of Morton:  521
matched idx of Morton:  522
matched idx of Morton:  523
matched idx of Morton:  526
matched idx of Morton:  529
matched idx of Morton:  531
matched idx of Morton:  533
matched idx of Morton:  535
matched idx of Morton:  536
matched idx of Morton:  537
matched idx of Morton:  541
matched idx of Morton:  543
matched idx of Morton:  546
matched idx of Morton:  547
matched idx of Morton:  549
matched idx of Morton:  550
matched idx of Morton:  556
matched idx of Morton:  557
matched idx of Morton:  559
matched idx of Morton:  560
matched idx of Morton:  561
matched idx of Morton:  562
matched idx of Morton:  565
matched idx of Morton:  566
matched idx of Morton:  567
matched idx of Morton:  568
matched idx of Morton:  569
matched idx of Morton:  572
matched idx of Morto

matched idx of Morton:  2061
matched idx of Morton:  2062
matched idx of Morton:  2063
matched idx of Morton:  2064
matched idx of Morton:  2065
matched idx of Morton:  2069
matched idx of Morton:  2070
matched idx of Morton:  2071
matched idx of Morton:  2076
matched idx of Morton:  2077
matched idx of Morton:  2093
matched idx of Morton:  2096
matched idx of Morton:  2097
matched idx of Morton:  2098
matched idx of Morton:  2104
matched idx of Morton:  2106
matched idx of Morton:  2108
matched idx of Morton:  2109
matched idx of Morton:  2111
matched idx of Morton:  2113
matched idx of Morton:  2118
matched idx of Morton:  2121
matched idx of Morton:  2122
matched idx of Morton:  2126
matched idx of Morton:  2128
matched idx of Morton:  2133
matched idx of Morton:  2134
matched idx of Morton:  2136
matched idx of Morton:  2138
matched idx of Morton:  2142
matched idx of Morton:  2147
matched idx of Morton:  2148
matched idx of Morton:  2153
matched idx of Morton:  2154
matched idx of

matched idx of Morton:  2835
matched idx of Morton:  2836
matched idx of Morton:  2837
matched idx of Morton:  2838
matched idx of Morton:  2843
matched idx of Morton:  2846
matched idx of Morton:  2847
matched idx of Morton:  2848
matched idx of Morton:  2852
matched idx of Morton:  2854
matched idx of Morton:  2857
matched idx of Morton:  2859
matched idx of Morton:  2862
matched idx of Morton:  2865
matched idx of Morton:  2866
matched idx of Morton:  2871
matched idx of Morton:  2872
matched idx of Morton:  2875
matched idx of Morton:  2877
matched idx of Morton:  2878
matched idx of Morton:  2881
matched idx of Morton:  2882
matched idx of Morton:  2888
matched idx of Morton:  2889
matched idx of Morton:  2890
matched idx of Morton:  2891
matched idx of Morton:  2895
matched idx of Morton:  2896
matched idx of Morton:  2897
matched idx of Morton:  2898
matched idx of Morton:  2903
matched idx of Morton:  2905
matched idx of Morton:  2907
matched idx of Morton:  2909
matched idx of

matched idx of Morton:  3576
matched idx of Morton:  3585
matched idx of Morton:  3589
matched idx of Morton:  3595
matched idx of Morton:  3596
matched idx of Morton:  3598
matched idx of Morton:  3599
matched idx of Morton:  3601
matched idx of Morton:  3603
matched idx of Morton:  3615
matched idx of Morton:  3616
matched idx of Morton:  3618
matched idx of Morton:  3623
matched idx of Morton:  3628
matched idx of Morton:  3639
matched idx of Morton:  3641
matched idx of Morton:  3643
matched idx of Morton:  3645
matched idx of Morton:  3649
matched idx of Morton:  3651
matched idx of Morton:  3659
matched idx of Morton:  3665
matched idx of Morton:  3666
matched idx of Morton:  3674
matched idx of Morton:  3675
matched idx of Morton:  3676
matched idx of Morton:  3679
matched idx of Morton:  3680
matched idx of Morton:  3683
matched idx of Morton:  3686
matched idx of Morton:  3687
matched idx of Morton:  3688
matched idx of Morton:  3690
matched idx of Morton:  3693
matched idx of

matched idx of Morton:  4390
matched idx of Morton:  4392
matched idx of Morton:  4395
matched idx of Morton:  4396
matched idx of Morton:  4402
matched idx of Morton:  4404
matched idx of Morton:  4405
matched idx of Morton:  4406
matched idx of Morton:  4407
matched idx of Morton:  4408
matched idx of Morton:  4409
matched idx of Morton:  4411
matched idx of Morton:  4418
matched idx of Morton:  4426
matched idx of Morton:  4437
matched idx of Morton:  4439
matched idx of Morton:  4441
matched idx of Morton:  4451
matched idx of Morton:  4452
matched idx of Morton:  4459
matched idx of Morton:  4460
matched idx of Morton:  4461
matched idx of Morton:  4462
matched idx of Morton:  4463
matched idx of Morton:  4468
matched idx of Morton:  4469
matched idx of Morton:  4470
matched idx of Morton:  4471
matched idx of Morton:  4476
matched idx of Morton:  4478
matched idx of Morton:  4481
matched idx of Morton:  4485
matched idx of Morton:  4486
matched idx of Morton:  4490
matched idx of

In [8]:
# new concat code
# Concatenate and clean up dataframes
if len(matched_events_mycatalog2morton)>0:
    matched_events_mycatalog2morton = pd.concat(matched_events_mycatalog2morton).reset_index(drop=True)
    matched_times_mycatalog2morton = matched_events_mycatalog2morton['datetime']
    lat_mycatalog2morton = matched_events_mycatalog2morton['latitude']
    lon_mycatalog2morton = matched_events_mycatalog2morton['longitude']

if len(matched_events_morton2mycatalog)>0:   
    matched_events_morton2mycatalog = pd.DataFrame(matched_events_morton2mycatalog).reset_index(drop=True)
    
if len(unmatched_events_anss2mycatalog)>0:
    unmatched_events_anss2mycatalog = pd.DataFrame(unmatched_events_anss2mycatalog).reset_index(drop=True)
    
if len(unmatched_events_morton2mycatalog)>0:
    unmatched_events_morton2mycatalog = pd.DataFrame(unmatched_events_morton2mycatalog).reset_index(drop=True)

if len(unmatched_events_mycatalog2morton_and_anss) > 0:
    unmatched_events_mycatalog2morton_and_anss = unmatched_events_mycatalog2morton_and_anss.reset_index(drop=True)

if len(matched_events_mycatalog2anss)>0:
    matched_events_mycatalog2anss = pd.concat(matched_events_mycatalog2anss).reset_index(drop=True)
    matched_times_mycatalog2anss = matched_events_mycatalog2anss['datetime']
    lat_mycatalog2anss = matched_events_mycatalog2anss['latitude']
    lon_mycatalog2anss = matched_events_mycatalog2anss['longitude']

if len(matched_events_anss2mycatalog)>0:   
    matched_events_anss2mycatalog = pd.DataFrame(matched_events_anss2mycatalog).reset_index(drop=True)
    matched_times_anss2mycatalog = matched_events_anss2mycatalog['datetime']

print(f"length of mycatalog:{len(mycatalog)}")
print(f"length of events_morton:{len(events_morton)}")
print(f"length of events_anss:{len(events_anss)}")
print(f"matched_events_mycatalog2morton:{len(matched_events_mycatalog2morton)}")
print(f"matched_events_morton2mycatalog:{len(matched_events_morton2mycatalog)}")
print(f"unmatched_events_anss2mycatalog:{len(unmatched_events_anss2mycatalog)}")
print(f"unmatched_events_morton2mycatalog:{len(unmatched_events_morton2mycatalog)}")
print(f"unmatched_events_mycatalog2morton_and_anss (new events):{len(unmatched_events_mycatalog2morton_and_anss)}")
print(f"matched_events_mycatalog2anss:{len(matched_events_mycatalog2anss)}")
print(f"matched_events_anss2mycatalog:{len(matched_events_anss2mycatalog)}")

length of mycatalog:18868
length of events_morton:5282
length of events_anss:131532
matched_events_mycatalog2morton:1374
matched_events_morton2mycatalog:1374
unmatched_events_anss2mycatalog:130763
unmatched_events_morton2mycatalog:3908
unmatched_events_mycatalog2morton_and_anss (new events):17116
matched_events_mycatalog2anss:769
matched_events_anss2mycatalog:769


In [9]:
# Save these three catalogs to csv files
matched_events_mycatalog2morton.to_csv('../data/datasets_pnsn_jdf/matched_events_with_morton_mycatalog.csv')
matched_events_anss2mycatalog.to_csv('../data/datasets_pnsn_jdf/matched_events_with_mycatalog_anss.csv')
matched_events_morton2mycatalog.to_csv('../data/datasets_pnsn_jdf/matched_events_with_mycatalog_morton.csv')
unmatched_events_mycatalog2morton_and_anss.to_csv('../data/datasets_pnsn_jdf/new_events.csv')
matched_events_mycatalog2anss.to_csv('../data/datasets_pnsn_jdf/matched_events_with_anss_mycatalog.csv')
unmatched_events_morton2mycatalog.to_csv('../data/datasets_pnsn_jdf/missing_events_from_mycatalog_morton.csv')
unmatched_events_anss2mycatalog.to_csv('../data/datasets_pnsn_jdf/missing_events_from_mycatalog_anss.csv')


## Plot the Origin Times

### Compare with Morton's Catalog 

In [ ]:
# Make lists for plotting the 1:1 line
x = pd.date_range(start='2011-1-1', end='2015-12-31', periods=len(matched_times_morton2mycatalog))
y = pd.date_range(start='2011-1-1', end='2015-12-31', periods=len(matched_times_morton2mycatalog))

# Plot the scatter plot
plt.figure()
plt.scatter(matched_times_mycatalog2morton,matched_times_morton2mycatalog)
plt.plot(x,y, 'k--')
plt.xlabel('Origin Time of mycatalog')
plt.ylabel('Origin Time of Morton')
plt.title('Scatter Plot: Origin Times of Matched Events')

### Compare with the ANSS Catalog 

In [ ]:
# Make lists for plotting the 1:1 line
matched_times_mycatalog2anss = pd.to_datetime(matched_times_mycatalog2anss)
matched_times_anss2mycatalog = pd.to_datetime(matched_times_anss2mycatalog)

x = pd.date_range(start='2014-1-1', end='2014-12-31', periods=len(matched_times_anss2mycatalog))
y = pd.date_range(start='2014-1-1', end='2014-12-31', periods=len(matched_times_anss2mycatalog))

# Plot the scatter plot
plt.figure()
plt.scatter(matched_times_mycatalog2anss,matched_times_anss2mycatalog)
plt.plot(x,y, 'k--')
plt.xlabel('Origin Time of mycatalog')
plt.ylabel('Origin Time of Morton')
plt.title('Scatter Plot: Origin Times of Matched Events')

## Plot the Latitudes

### Compare with Morton's Catalog 

In [ ]:
# Plot the scatter plot
plt.figure()
lat_min = min(lat_mycatalog2morton)
lat_max = max(lat_mycatalog2morton)

# Make lists for plotting the 1:1 line
x_lat = np.linspace(lat_min, lat_max, 10)
y_lat = np.linspace(lat_min, lat_max, 10)
plt.scatter(lat_mycatalog2morton,lat_morton2mycatalog, s=15)
plt.plot(x_lat,y_lat, 'k--')
plt.xlabel('Latitudes of Our Catalog ($^\circ$)')
plt.ylabel('Latitudes of Morton et al. (2023) ($^\circ$)')
plt.title('Latitudes of Our Catalog vs.Latitudes of Morton et al. (2023)')

### Compare with the ANSS Catalog 

In [ ]:
# Plot the scatter plot
plt.figure()
lat_min = min(lat_mycatalog2anss)
lat_max = max(lat_mycatalog2anss)

# Make lists for plotting the 1:1 line
x_lat = np.linspace(lat_min, lat_max, 10)
y_lat = np.linspace(lat_min, lat_max, 10)
plt.scatter(lat_mycatalog2anss,lat_anss2mycatalog, s=15)
plt.plot(x_lat,y_lat, 'k--')
plt.xlabel('Latitudes of Our Catalog ($^\circ$)')
plt.ylabel('Latitudes of ANSS Catalog ($^\circ$)')
plt.title('Latitudes of Our Catalog vs. ANSS Catalog')

## Plot the Longitudes

### Compare with Morton's Catalog 

In [ ]:
# Plot the scatter plot
plt.figure()
lon_min = min(lon_mycatalog2morton)
lon_max = max(lon_mycatalog2morton)

# Make lists for plotting the 1:1 line
x_lon = np.linspace(lon_min, lon_max, 10)
y_lon = np.linspace(lon_min, lon_max, 10)
plt.scatter(lon_mycatalog2morton,lon_morton2mycatalog)
plt.plot(x_lon,y_lon, 'k--')
plt.xlabel('Longitudes of Our Catalog ($^\circ$)')
plt.ylabel('Longitudes of Morton et al. (2023) ($^\circ$)')
plt.title('Longitudes of Our Catalog vs.Latitudes of Morton et al. (2023)')

### Compare with the ANSS Catalog 

In [ ]:
# Plot the scatter plot
plt.figure()
lon_min = min(lon_mycatalog2anss)
lon_max = max(lon_mycatalog2anss)

# Make lists for plotting the 1:1 line
x_lon = np.linspace(lon_min, lon_max, 10)
y_lon = np.linspace(lon_min, lon_max, 10)
plt.scatter(lon_mycatalog2anss,lon_anss2mycatalog)
plt.plot(x_lon,y_lon, 'k--')
plt.xlabel('Longitudes of Our Catalog ($^\circ$)')
plt.ylabel('Longitudes of Morton et al. (2023) ($^\circ$)')
plt.title('Longitudes of Our Catalog vs.Latitudes of Morton et al. (2023)')

## Histograms
Make histograms of mycatalog vs. Morton's catalog

### Histogram: All of our catalog 

In [ ]:
events = pd.read_csv('../../data/datasets_all_years/events_pnsn_wa.csv')

In [ ]:
# Plot the same histogram but overlay the histograms
bins = np.linspace(5,30,25)

plt.hist(unmatched_events_mycatalog2morton_and_anss['picks'], bins=bins,  
         alpha=0.5, # the transaparency parameter 
         label='Newly detected events') 
plt.hist(matched_events_mycatalog2anss['picks'], bins=bins,
         alpha=0.5, 
         label='Events matching the ANSS Catalog')   
plt.hist(matched_events_mycatalog2morton['picks'], bins=bins,
         alpha=0.5, 
         label='Events matching Morton et al., 2023') 

plt.xlabel('Number of Picks')
plt.ylabel('Number of Events')  
plt.legend(loc='upper right') 
plt.title('Picks vs. Number of Events') 
plt.show()


### Histogram: Matched events alone

### Compare with Morton et al. (2023)

In [ ]:
# Plot the histogram of the number of picks for the matched events
plt.figure()
bins = np.linspace(5,30,25)
plt.hist(matched_events_mycatalog2morton['picks'],bins=bins)
plt.xlabel('Number of Picks')
plt.ylabel('Number of Events')
plt.title('Histogram of Matched Events with Morton et al. (2023): Picks vs. the Number of Events')

### Compare with ANSS 

In [ ]:
# Plot the histogram of the number of picks for the matched events
plt.figure()
bins = np.linspace(5,30,25)
plt.hist(matched_events_mycatalog2anss['picks'],bins=bins)
plt.xlabel('Number of Picks')
plt.ylabel('Number of Events')
plt.title('Histogram of Matched Events with ANSS: Picks vs. the Number of Events')

## 2. Filter events 
Filter Events based on the following criteria
1. For an event, at least two stations have to be less than 50 km from the event and no station can be 100 km apart from each other.
2. An event has to have more than or equal to 6 picks


In [10]:
# Read the new events file
year= 'pnsn_jdf'
events = pd.read_csv(f'../data/datasets_{year}/new_events.csv')
events

Unnamed: 0.1  Unnamed: 0    idx                              time  \
0                 0           0      2  2011-12-10 22:44:46.018805+00:00   
1                 1           6      3  2011-12-26 18:06:15.493905+00:00   
2                 2          12      8  2012-02-04 20:05:31.130689+00:00   
3                 3          25     16  2012-03-18 18:48:43.937964+00:00   
4                 4          39     25  2012-06-12 23:24:49.130015+00:00   
...             ...         ...    ...                               ...   
17111         17111      173740  30598  2015-09-13 13:18:05.562213+00:00   
17112         17112      173759  30603  2015-09-14 05:33:02.229963+00:00   
17113         17113      173769  30604  2015-09-14 06:09:08.238133+00:00   
17114         17114      173779  30605  2015-09-14 13:34:01.138138+00:00   
17115         17115      173788  30609  2015-09-15 09:12:54.234894+00:00   

                x           y          z  picks   latitude   longitude  \
0      -96.503032   58.401356  12.890625      6  45.018973 -126.724334   
1      -36.258365  132.782258  41.015625      6  45.693849 -125.965511   
2     -203.604662  483.230738  49.609375      7  48.813643 -128.272371   
3      185.754391  252.936022  25.390625      8  46.749918 -123.068939   
4     -179.060539  533.294806  49.609375      6  49.270955 -127.960611   
...           ...         ...        ...    ...        ...         ...   
17111 -161.210267 -403.618477  30.859375      6  40.850788 -127.411729   
17112  -60.802488 -370.719232   0.390625     10  41.160599 -126.224435   
17113 -145.591279 -447.960938  49.609375     10  40.454578 -127.216333   
17114 -161.210267 -435.087320  49.609375      9  40.567566 -127.403644   
17115 -142.244353 -277.743104  16.015625      6  41.987174 -127.216502   

           depth  event_idx  pick_idx  residual station phase     time_pick  \
0      12.890625          2   1655834  0.530519    J35A     P  1.323557e+09   
1      41.015625          3   1654163 -0.561964    J35A     P  1.324923e+09   
2      49.609375          8    345847 -1.158387    J35A     P  1.328386e+09   
3      25.390625         16    129536 -0.081932    J35A     P  1.332097e+09   
4      49.609375         25    207246 -0.017101    J43A     P  1.339544e+09   
...          ...        ...       ...       ...     ...   ...           ...   
17111  30.859375      30598   2817970  0.051799    G10D     S  1.442150e+09   
17112   0.390625      30603   1476568  0.078527    G10D     P  1.442209e+09   
17113  49.609375      30604   1476574 -0.531605    G10D     P  1.442211e+09   
17114  49.609375      30605   1476584  0.303990    G10D     P  1.442238e+09   
17115  16.015625      30609   1452051 -0.035427    G10D     P  1.442308e+09   

                               datetime  
0      2011-12-10 22:44:46.018805+00:00  
1      2011-12-26 18:06:15.493905+00:00  
2      2012-02-04 20:05:31.130689+00:00  
3      2012-03-18 18:48:43.937964+00:00  
4      2012-06-12 23:24:49.130015+00:00  
...                                 ...  
17111  2015-09-13 13:18:05.562213+00:00  
17112  2015-09-14 05:33:02.229963+00:00  
17113  2015-09-14 06:09:08.238133+00:00  
17114  2015-09-14 13:34:01.138138+00:00  
17115  2015-09-15 09:12:54.234894+00:00  

[17116 rows x 18 columns]

In [11]:
all_pick_assignments = pd.read_csv(f'../data/datasets_{year}/all_pick_assignments_{year}.csv')
mycatalog = all_pick_assignments.drop_duplicates(subset=['idx'])
mycatalog

Unnamed: 0    idx                              time           x  \
0                0      2  2011-12-10 22:44:46.018805+00:00  -96.503032   
6                6      3  2011-12-26 18:06:15.493905+00:00  -36.258365   
12              12      8  2012-02-04 20:05:31.130689+00:00 -203.604662   
19              19      9  2012-02-06 08:17:12.331083+00:00  -71.958908   
25              25     16  2012-03-18 18:48:43.937964+00:00  185.754391   
...            ...    ...                               ...         ...   
173759      173759  30603  2015-09-14 05:33:02.229963+00:00  -60.802488   
173769      173769  30604  2015-09-14 06:09:08.238133+00:00 -145.591279   
173779      173779  30605  2015-09-14 13:34:01.138138+00:00 -161.210267   
173788      173788  30609  2015-09-15 09:12:54.234894+00:00 -142.244353   
173794      173794  30610  2015-09-15 17:31:03.266140+00:00   71.958908   

                 y          z  picks   latitude   longitude      depth  \
0        58.401356  12.890625      6  45.018973 -126.724334  12.890625   
6       132.782258  41.015625      6  45.693849 -125.965511  41.015625   
12      483.230738  49.609375      7  48.813643 -128.272371  49.609375   
19     -123.259693   1.171875      6  43.387215 -126.388083   1.171875   
25      252.936022  25.390625      8  46.749918 -123.068939  25.390625   
...            ...        ...    ...        ...         ...        ...   
173759 -370.719232   0.390625     10  41.160599 -126.224435   0.390625   
173769 -447.960938  49.609375     10  40.454578 -127.216333  49.609375   
173779 -435.087320  49.609375      9  40.567566 -127.403644  49.609375   
173788 -277.743104  16.015625      6  41.987174 -127.216502  16.015625   
173794 -465.125761  47.265625      6  40.309645 -124.653498  47.265625   

        event_idx  pick_idx  residual station phase     time_pick  
0               2   1655834  0.530519    J35A     P  1.323557e+09  
6               3   1654163 -0.561964    J35A     P  1.324923e+09  
12              8    345847 -1.158387    J35A     P  1.328386e+09  
19              9    121103 -0.167694    J35A     P  1.328516e+09  
25             16    129536 -0.081932    J35A     P  1.332097e+09  
...           ...       ...       ...     ...   ...           ...  
173759      30603   1476568  0.078527    G10D     P  1.442209e+09  
173769      30604   1476574 -0.531605    G10D     P  1.442211e+09  
173779      30605   1476584  0.303990    G10D     P  1.442238e+09  
173788      30609   1452051 -0.035427    G10D     P  1.442308e+09  
173794      30610   1452085  0.084264    G10D     P  1.442338e+09  

[18868 rows x 16 columns]

In [12]:
count = 0

In [19]:
"""
Inputs:
1. Either of the following files can be the input:
    1. matched_events_with_morton_mycatalog.csv from the 4_quality_control file
    2. matched_events_with_anss_mycatalog.csv from the 4_quality_control file
    3. new_events.csv from the 4_quality_control file
2. The all_pick_assignments CSV file from the 3_associate file: e.g., all_pick_assignments = pd.read_csv('../data/datasets_2012/all_pick_assignments_2012.csv')


Outputs:
1. A new dataframe that only has events that fall into the following categories:
    1. For an event, at least two stations have to be less than 50 km from the event and no station can be 100 km apart from each other.
2. An event has to have more than or equal to 6 picks
"""

# Parameters
client2 = Client("IRIS")

mycatalog = all_pick_assignments.drop_duplicates(subset=['idx'])
mycatalog['datetime'] = pd.to_datetime(mycatalog['time'], utc = True)

for i, idx in tqdm(enumerate(events['idx']),total=len(events['idx'])):
    event = mycatalog
    picks = all_pick_assignments
    picks_idx = picks.loc[picks['idx']==idx]
    pick_sta = np.unique(picks_idx['station'])
    otime = UTCDateTime(str(event[event['idx'] == idx]["datetime"].values[0]))
    distances = []
    max_dist = 10
    min_dist = 0
    for station in pick_sta:


        sta_inv = client2.get_stations(network='*',
                                       station=station, channel="?H?", 
                                       starttime=otime - 1e8, endtime=otime + 1e8,level="response")
        if len(sta_inv) == 0:
            print(f"Failed to fetch for {networks} {station} {otime}")
            continue

        _network = sta_inv[0].code
        slat = sta_inv[0][0].latitude
        slon = sta_inv[0][0].longitude
        olat = event.loc[event['idx']==idx, 'latitude'].values[0]
        olon = event.loc[event['idx']==idx, 'longitude'].values[0]

        dis1 = locations2degrees(olat, olon, slat, slon)
        dist = degrees2kilometers(dis1)

        distances.append([None, _network, station, dist])

    # Sort distances
    distances = sorted(distances, key=lambda item: item[-1])

    # This is for the first criterion in the markdown above
    # Determine if any two of the numbers in the distances list are less than or equal to 50
    found = False
    for i in range(len(distances)):
        for j in range(i + 1, len(distances)):
            if distances[i][3] <= 50 and distances[j][3] <= 50:
                found = True
                break
        if found:
            break

    # Make a list that includes the differences between the consecutive numbers in the distances list.
    differences = [distances[i+1][3] - distances[i][3] for i in range(len(distances) - 1)]

    if found == False: # If there were not at least two distances between the station and the event less than or equal to 50 km
        print(distances)
        index = events[events['idx'] == idx].index
        events = events.drop(index=index)

    elif any(differences > 100 for differences in differences): # If any of the distances between two stations were greater than 100 km
        print(distances)
        index = events[events['idx'] == idx].index
        events = events.drop(index=index)

    else: 
        continue


events 

/tmp/ipykernel_2254968/2718798803.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mycatalog['datetime'] = pd.to_datetime(mycatalog['time'], utc = True)
  1%|          | 166/16859 [02:23<4:48:42,  1.04s/it]

[[None, '7D', 'G35B', 57.69199491736217], [None, '7D', 'G36B2', 68.31007432557199], [None, 'X9', 'BB060', 85.90605460848693], [None, 'X9', 'BB070', 136.58446786417755]]


  1%|          | 168/16859 [02:24<4:07:17,  1.12it/s]

[[None, '7D', 'FS20B', 26.15357908051852], [None, '7D', 'FS13B', 27.47736589383104], [None, '7D', 'FS06B', 36.77800843020512], [None, '7D', 'FS02B', 38.593840014520964], [None, 'X9', 'BB070', 308.20356045812144]]


  1%|          | 169/16859 [02:25<3:47:56,  1.22it/s]

...

100%|█████████▉| 16858/16859 [4:12:41<00:00,  1.27it/s]

[[None, 'Z5', 'GB331', 69.52694922166272], [None, 'Z5', 'GB281', 121.88012625764327], [None, '7D', 'G10D', 157.86900757698763], [None, 'Z5', 'GB101', 175.3392665879465], [None, '7D', 'G26D', 235.48673091891624]]


100%|██████████| 16859/16859 [4:12:41<00:00,  1.11it/s]

[[None, 'Z5', 'GB101', 52.064659969839596], [None, 'Z5', 'GB281', 142.00643865675804], [None, '7D', 'G26D', 157.7157381844174], [None, '7D', 'G10D', 192.30158076857666]]


Unnamed: 0.1  Unnamed: 0    idx                              time  \
14               14         125     43  2012-09-03 20:50:03.350437+00:00   
15               15         132     44  2012-09-03 21:04:23.707023+00:00   
17               17         150     46  2012-09-04 01:39:12.741518+00:00   
18               18         161     47  2012-09-04 05:14:30.296996+00:00   
23               23         239     61  2012-09-05 02:21:21.447436+00:00   
...             ...         ...    ...                               ...   
17075         17075      173421  30534  2015-09-07 11:42:50.035937+00:00   
17081         17081      173464  30542  2015-09-07 23:58:49.808213+00:00   
17084         17084      173495  30549  2015-09-08 16:45:36.023145+00:00   
17108         17108      173708  30594  2015-09-13 02:25:30.084615+00:00   
17112         17112      173759  30603  2015-09-14 05:33:02.229963+00:00   

               x           y          z  picks   latitude   longitude  \
14     16.176809 -425.074506   0.390625      7  40.673262 -125.308670   
15     79.768402 -460.834555  27.734375     12  40.347576 -124.561106   
17     60.802488 -429.365712  44.921875     11  40.632541 -124.781303   
18      7.251673 -446.530536  45.703125      8  40.480171 -125.414478   
23     60.802488 -455.112947  30.859375     10  40.400696 -124.783775   
...          ...         ...        ...    ...        ...         ...   
17075   0.557821 -375.010438  12.890625      7  41.124237 -125.493357   
17081 -19.523735 -334.959183  33.984375      7  41.484628 -125.733773   
17084 -25.101945 -354.984810  41.015625      6  41.304164 -125.799734   
17108 -61.918130 -392.175261   0.390625      7  40.967329 -126.235570   
17112 -60.802488 -370.719232   0.390625     10  41.160599 -126.224435   

           depth  event_idx  pick_idx  residual station phase     time_pick  \
14      0.390625         43    137797  0.168853   FS01B     P  1.346705e+09   
15     27.734375         44    137798 -0.748333   FS01B     P  1.346706e+09   
17     44.921875         46     84891 -0.517545   FS01B     P  1.346723e+09   
18     45.703125         47     84895 -0.511428   FS01B     P  1.346736e+09   
23     30.859375         61     12601 -1.225561   FS01B     P  1.346812e+09   
...          ...        ...       ...       ...     ...   ...           ...   
17075  12.890625      30534   1639962 -1.253627    G10D     P  1.441626e+09   
17081  33.984375      30542   1152741  0.323526    G18D     P  1.441670e+09   
17084  41.015625      30549   1315524 -0.664551    G10D     P  1.441731e+09   
17108   0.390625      30594   2817933  0.111715    G10D     S  1.442111e+09   
17112   0.390625      30603   1476568  0.078527    G10D     P  1.442209e+09   

                               datetime  
14     2012-09-03 20:50:03.350437+00:00  
15     2012-09-03 21:04:23.707023+00:00  
17     2012-09-04 01:39:12.741518+00:00  
18     2012-09-04 05:14:30.296996+00:00  
23     2012-09-05 02:21:21.447436+00:00  
...                                 ...  
17075  2015-09-07 11:42:50.035937+00:00  
17081  2015-09-07 23:58:49.808213+00:00  
17084  2015-09-08 16:45:36.023145+00:00  
17108  2015-09-13 02:25:30.084615+00:00  
17112  2015-09-14 05:33:02.229963+00:00  

[4363 rows x 18 columns]

In [ ]:
new_events_filtered = filter_sta(new_events, mycatalog_picks)

In [ ]:
new_events_filtered.to_csv(f'../data/datasets_{year}/new_events_filtered_pnsn_wa.csv')

In [21]:
events.to_csv(f'../data/datasets_{year}/new_events_filtered_{year}.csv')

In [26]:
events

Unnamed: 0.1  Unnamed: 0     idx                              time  \
2                 2          22       9  2011-01-01 21:15:59.281683+00:00   
13               13         160      34  2011-01-03 07:33:08.560877+00:00   
15               15         207      39  2011-01-03 08:33:59.698375+00:00   
17               17         220      41  2011-01-03 09:42:18.324354+00:00   
19               19         239      43  2011-01-03 11:03:16.972894+00:00   
...             ...         ...     ...                               ...   
77999         77999      734115  196379  2015-12-30 01:54:02.995317+00:00   
78009         78009      734272  196395  2015-12-31 08:12:36.917788+00:00   
78010         78010      734278  196396  2015-12-31 09:42:08.772727+00:00   
78011         78011      734285  196397  2015-12-31 14:01:51.097809+00:00   
78013         78013      734299  196400  2015-12-31 16:08:33.417892+00:00   

                x           y          z  picks   latitude   longitude  \
2      178.932677  466.679734   8.984375      7  48.672531 -123.070417   
13     116.327390 -422.409232  47.265625     10  40.689219 -124.123839   
15     119.711460 -392.493722  31.640625      7  40.958039 -124.078076   
17     141.707912 -459.504465  49.609375     10  40.351336 -123.831996   
19     192.468955  460.696632   0.390625     13  48.614762 -122.889588   
...           ...         ...        ...    ...        ...         ...   
77999   79.102626 -427.195714  33.203125      6  40.650531 -124.564744   
78009   83.332712 -430.785575   1.171875      6  40.617793 -124.515212   
78010  195.007007 -452.324742   4.296875      7  40.405197 -123.202845   
78011  185.700816 -467.880808  48.046875      7  40.267332 -123.316911   
78013   86.716782 -430.785575  18.359375      6  40.617445 -124.475227   

           depth  event_idx  pick_idx  residual station phase     time_pick  \
2       8.984375          9  17476232  1.021405    LRIV     S  1.293917e+09   
13     47.265625         34   9298994  0.108464     JCC     P  1.294040e+09   
15     31.640625         39   9298998  0.002486     JCC     P  1.294044e+09   
17     49.609375         41   9299000 -0.187211     JCC     P  1.294048e+09   
19      0.390625         43   9900576  0.831680    LRIV     P  1.294053e+09   
...          ...        ...       ...       ...     ...   ...           ...   
77999  33.203125     196379   8780969 -0.090423     JCC     P  1.451440e+09   
78009   1.171875     196395   8066503  0.018756     JCC     P  1.451550e+09   
78010   4.296875     196396   8066506  0.429082     JCC     P  1.451555e+09   
78011  48.046875     196397   8066510  0.177298     JCC     P  1.451571e+09   
78013  18.359375     196400   8066517  0.016042     JCC     P  1.451578e+09   

                               datetime  
2      2011-01-01 21:15:59.281683+00:00  
13     2011-01-03 07:33:08.560877+00:00  
15     2011-01-03 08:33:59.698375+00:00  
17     2011-01-03 09:42:18.324354+00:00  
19     2011-01-03 11:03:16.972894+00:00  
...                                 ...  
77999  2015-12-30 01:54:02.995317+00:00  
78009  2015-12-31 08:12:36.917788+00:00  
78010  2015-12-31 09:42:08.772727+00:00  
78011  2015-12-31 14:01:51.097809+00:00  
78013  2015-12-31 16:08:33.417892+00:00  

[26691 rows x 18 columns]

In [ ]:
count = 0
for i, idx in enumerate(range(0,10,1)):
    print(i,idx,count)
    count+=1

print(count)

In [ ]:
new_events

## Plot using the plotting functions

In [ ]:
all_picks = pd.read_csv('../data/datasets_2014/all_picks_2014_for_assoc.csv')

In [ ]:
all_picks

In [ ]:
all_picks_networks = all_picks['station_network_code'].drop_duplicates()
list_networks = list(all_picks_networks)
all_picks_networks = ','.join(all_picks_networks)
all_picks_networks

In [ ]:
list_networks

In [ ]:
# Clean up the memory
del all_picks

## Plot the offshore events north of 44&deg; N

In [ ]:
new_events = pd.read_csv('../data/datasets_2014/new_events.csv')

In [ ]:
new_events_44N_and_above= new_events.loc[(new_events['latitude']>44)&(new_events['longitude']<-124)]
new_events_44N_and_above = new_events_44N_and_above[0:50] 

In [ ]:
# parameters for subplots_cluster_scale
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "?H?"
idx_sta= 50
title= "Events matched"
fig_title= "new_events_filtered_44N_and_above_plots.pdf"

subplots_cluster_scale(new_events_44N_and_above,mycatalog_picks,networks,channel,idx_sta,title,fig_title)

## Plot one of the cluster events at around 46.5&deg; N, 125&deg; W using the plotting functions 

In [ ]:
def subplots_cluster_scale_p(idx, mycatalog, mycatalog_picks, networks, channel, idx_sta, title, fig_title):
    """
    idx: event_idx
    mycatalog: dataframe that contains only the unique picks (i.e., mycatalog_picks.drop_duplicates(subset=['idx']).copy())
    mycatalog_picks: all pick assignments csv file (e.g., pd.read_csv('../data/datasets_OR/all_pick_assignments_OR.csv'))
    networks: string of networks (e.g., "NV,OO,7A")
    channel: specify the direction of the channel (i.e., "?HZ", "?HE" or "?HN")
    idx_sta: choose the station to which you want to show the waveforms
    title: title in a string
    fig_title: figure title in as string
    """
        
    # Define the clients 
    client_waveform = WaveformClient()
    client2 = Client("IRIS")
    client_ncedc = Client('NCEDC')


    # Plot the earthquake moveout for one of the unmatched events for all stations 
    event = mycatalog
    picks = mycatalog_picks
    picks_idx = picks.loc[picks['idx']==idx]
    pick_sta = np.unique(picks_idx['station'])
    
    otime = UTCDateTime(str(event[event['idx'] == idx]["datetime"].values[0]))
    distances = []
    max_dist = 10
    min_dist = 0
    
    print(event[event['idx'] == idx]['picks'].values[0])
    for station in pick_sta:
        
        
        sta_inv = client2.get_stations(network=networks,
                                       station=station, channel="?H?", 
                                       starttime=otime - 1e8, endtime=otime + 1e8,level="response")
        if len(sta_inv) == 0:
#             print(f"Failed to fetch for {networks} {station} {otime}")
            continue
            
        _network = sta_inv[0].code
        slat = sta_inv[0][0].latitude
        slon = sta_inv[0][0].longitude
        olat = event.loc[event['idx']==idx, 'latitude'].values[0]
        olon = event.loc[event['idx']==idx, 'longitude'].values[0]
        
        dis1 = locations2degrees(olat, olon, slat, slon)
        dist = degrees2kilometers(dis1)
#         if max_dist < dist:
#             max_dist = dist
            
#         if min_dist > dist:
#             min_dist = dist
            
        distances.append([None, _network, station, dist])

    # Sort distances
    distances = sorted(distances, key=lambda item: item[-1])
    distances = distances[:idx_sta+1]
    
    # Set up to define the xlim and ylim
    max_y = 0
    min_y = 0
    # This count is for the if statements. Only used to ensure that min_y_count 
    #is changed from 0 to either the first positive value of the distance of one of the stations from the event
    min_y_count = 0 
    
    max_x = 0
    min_x = 0
    
    # This count is for the if statements. Only used to ensure that min_x_count 
    #is changed from 0 to either the first positive value of P pick time or the first positive value of S pick time
    min_x_count= 0
    # Create a figure
    fig,axs = plt.subplots(1,4,figsize=(18,6))
    gs = fig.add_gridspec(3, hspace=0, figure=fig)
#     axs = gs.subplots(sharex=True, sharey=True)
    starttime = otime -30
    endtime = otime + 120
    
    # Define texts
    texts = []
    
    for i, ii in enumerate(distances):
            
        if ii[1] in ['NC', 'BK']:
            # Query waveforms
            st = client_ncedc.get_waveforms(network=ii[1], station=ii[2], location="*", channel=channel,starttime=starttime, endtime=endtime)

        elif ii[1] in networks: 
            st = client_waveform.get_waveforms(network=ii[1], station=ii[2], channel=channel,starttime=starttime, endtime=endtime)
  
        else: 
            st =  Stream()
            print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
            continue
            
#         print(f"len(st):{len(st)}")
#         print(st)
    
        # Skip empty traces
        if len(st) == 0:
                continue
                
        sta_picks = picks_idx[picks_idx['station'] == ii[2]]
        p_picks = sta_picks.loc[sta_picks['phase'] == 'P']
        s_picks = sta_picks.loc[sta_picks['phase'] == 'S']
#         print(len(p_picks),len(s_picks))
        
        # Define the xlim values
        # Define the maximum x value
        if len(s_picks) > 0:
            if max_x < UTCDateTime(s_picks.iloc[0]['time_pick']) - starttime:
                max_x = UTCDateTime(s_picks.iloc[0]['time_pick']+5) - starttime
        elif len(p_picks) > 0:
            if max_x < UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime: 
                max_x = UTCDateTime(p_picks.iloc[0]['time_pick']+5) - starttime
        else:
            print('No picks for this station. Skipping.')
            continue 
            
        # Define the minimum x value
        if len(p_picks) > 0:
            if min_x_count == 0:
                if min_x < UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime:
                    min_x = UTCDateTime(p_picks.iloc[0]['time_pick']-5) - starttime
                    min_x_count += 1           
            else:
                if min_x >= UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime:
                    min_x = UTCDateTime(p_picks.iloc[0]['time_pick']-5) - starttime            
        elif len(s_picks) > 0:
            if min_x_count == 0:
                if min_x < UTCDateTime(s_picks.iloc[0]['time_pick'])- starttime:
                    min_x = UTCDateTime(s_picks.iloc[0]['time_pick']-5)- starttime
                    min_x_count += 1                
            else:
                if min_x >= UTCDateTime(s_picks.iloc[0]['time_pick'])- starttime:
                    min_x = UTCDateTime(s_picks.iloc[0]['time_pick']-5) - starttime
        else:
            print('No picks for this station. Skipping.')
            continue    
            
        if len(p_picks) == 0:
            continue
            
#         print('This is after the p_pick continue statement')
    
        # Define ylim values
        if min_y_count == 0:
            if min_y < ii[3]:
                min_y = ii[3] - 5
                min_y_count += 1           
        else:
            if min_y >= ii[3]:
                min_y = ii[3] - 5 
                
        max_y = ii[3] + 5
        
    scaling_factor = (1/2)*(max_y-min_y)   
        
    for i, ii in enumerate(distances):
            
        if ii[1] in ['NC', 'BK']:
            # Query waveforms
            st = client_ncedc.get_waveforms(network=ii[1], station=ii[2], location="*", channel=channel,starttime=starttime, endtime=endtime)

        elif ii[1] in networks: 
            st = client_waveform.get_waveforms(network=ii[1], station=ii[2], channel=channel,starttime=starttime, endtime=endtime)
  
        else: 
            st =  Stream()
            print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
            continue
            
#         print(f"len(st):{len(st)}")
#         print(st)
    
        # Skip empty traces
        if len(st) == 0:
                continue
        _st = Stream()
        # Check for HH and BH channels presence
        has_HH = bool(st.select(channel="HH?"))
        has_BH = bool(st.select(channel="BH?"))

        # Apply selection logic based on channel presence
        if has_HH and has_BH:
            # If both HH and BH channels are present, select only HH
            _st += st.select(channel="HH?")
        elif has_HH:
            # If only HH channels are present
            _st += st.select(channel="HH?")
        elif has_BH:
            # If only BH channels are present
            _st += st.select(channel="BH?")

        st = _st

        print(f'Second st print:{_st}')
              
        st = Stream(filter(lambda st: st.stats.sampling_rate > 10, st))
        st.taper(max_percentage=0.05)
        st.filter(type='bandpass', freqmin=2, freqmax=25)
        st.merge(fill_value='interpolate') # fill gaps if there are any.

#         print(st)
        # Select only one trace per channel
        unique_channels = set(tr.stats.channel for tr in st)
        selected_traces = []
        
        for ch in unique_channels:
            selected_traces.append(next(tr for tr in st if tr.stats.channel == ch))
        st = Stream(selected_traces)
                   
        trim_st = st.copy()
        sta_picks = picks_idx[picks_idx['station'] == ii[2]]
        p_picks = sta_picks.loc[sta_picks['phase'] == 'P']
        s_picks = sta_picks.loc[sta_picks['phase'] == 'S']
#         print(len(p_picks),len(s_picks))
        
        
                
            
        if len(p_picks) == 0:
            continue 
#         print('This is after the p_pick continue statement')
        print(trim_st)
        
        for iax in range(len(trim_st)):
            print(iax)
            sampling_rate = trim_st[iax].stats.sampling_rate
            trim_st = trim_st.normalize()
            
            tp = UTCDateTime(p_picks.iloc[0]['time_pick']) - otime + 30
            i1 = int((tp-5)*sampling_rate)
            i2 = int((tp+15)*sampling_rate)

            offsets1 = ii[3]
            try: 
                wave = trim_st[iax].data
                wave = wave / (np.nanmax(wave[i1:i2], axis=-1)*10)
            except:
                continue 
            
#             print(trim_st[iax].stats.sampling_rate)
            axs[iax].plot(trim_st[iax].times(), wave * scaling_factor + offsets1, 
                          color='black', label=f"{trim_st[iax].stats.channel}", alpha=0.7, lw=0.5)
#             axs[iax].plot(trim_st[iax].times(), wave * 30 + offsets1, color='black', label=f"{trim_st[iax].stats.channel}", alpha=0.7, lw=0.5)

#             axs[iax].text(xlim[-1] + 2,   offsets1, 
#                               [ii[2]], fontsize=8, verticalalignment='bottom')

            if len(p_picks) > 0:
                axs[iax].vlines(UTCDateTime(p_picks.iloc[0]['time_pick']) - otime + 30, offsets1 - (1/35) * scaling_factor, 
                                offsets1 + (1/35) * scaling_factor, color='r')
            if len(s_picks) > 0:
                axs[iax].vlines(UTCDateTime(s_picks.iloc[0]['time_pick']) - otime + 30, offsets1 - (1/35) * scaling_factor, 
                                offsets1 + (1/35) * scaling_factor, color='b')
        texts.append([ii[2],ii[3]])

    
#     print(max_y,min_y)
    chs = ['2','1','Z']
    for iax in range(3):
        for i, ii in enumerate(texts):
            offsets1 = ii[1]
            axs[iax].text(max_x + 0.5, offsets1, 
                                  [ii[0]], fontsize=8, verticalalignment='bottom')
        axs[iax].legend(chs[iax],loc='upper right', handlelength=0)
        axs[iax].set_ylim([min_y,max_y])
        axs[iax].set_xlim([min_x,max_x])
        axs[iax].grid(alpha=0.5)
    fig.supxlabel('Time [sec]', y=0.07)
    fig.supylabel('Distance [km]')
    fig.suptitle(f"{title}: Origin Time={otime}, \n Latitude={round(event[event['idx']==idx]['latitude'].values[0], 2)}, Longtitude={round(event[event['idx']==idx]['longitude'].values[0], 2)}, Depth={round(event[event['idx']==idx]['depth'].values[0], 2)}", y=1)
    
    m = Basemap(projection='merc', llcrnrlat=40, urcrnrlat=50, llcrnrlon=-130, urcrnrlon=-120, resolution='i', ax=axs[3])
    m.drawcoastlines()
    m.drawcountries()
    m.drawstates()
    m.drawmapboundary()
    m.drawparallels(np.arange(40, 51, 1), labels=[1,0,0,0])
    m.drawmeridians(np.arange(-130, -119, 1), labels=[0,0,0,1])
    x, y = m(event[event['idx']==idx]['longitude'].values[0], event[event['idx']==idx]['latitude'].values[0])
    m.plot(x, y, 'ro', markersize=9)
    axs[3].set_title('Event Location')
    
    plt.show()


In [ ]:
def subplots_cluster_scale(idx, mycatalog, mycatalog_picks, networks, channel, idx_sta, title, fig_title):
    """
    idx: event_idx
    mycatalog: dataframe that contains only the unique picks (i.e., mycatalog_picks.drop_duplicates(subset=['idx']).copy())
    mycatalog_picks: all pick assignments csv file (e.g., pd.read_csv('../data/datasets_OR/all_pick_assignments_OR.csv'))
    networks: string of networks (e.g., "NV,OO,7A")
    channel: specify the direction of the channel (i.e., "?HZ", "?HE" or "?HN")
    idx_sta: choose the station to which you want to show the waveforms
    title: title in a string
    fig_title: figure title in as string
    """
        
    # Define the clients 
    client_waveform = WaveformClient()
    client2 = Client("IRIS")
    client_ncedc = Client('NCEDC')


    # Plot the earthquake moveout for one of the unmatched events for all stations 
    event = mycatalog
    picks = mycatalog_picks
    
    p = PdfPages(fig_title) 
    
    for idx in event['idx']:
        
        picks_idx = picks.loc[picks['idx']==idx]
        pick_sta = np.unique(picks_idx['station'])

        otime = UTCDateTime(str(event[event['idx'] == idx]["datetime"].values[0]))
        distances = []
        max_dist = 10
        min_dist = 0

        print(event[event['idx'] == idx]['picks'].values[0])
        for station in pick_sta:


            sta_inv = client2.get_stations(network=networks,
                                           station=station, channel="?H?", 
                                           starttime=otime - 1e8, endtime=otime + 1e8,level="response")
            if len(sta_inv) == 0:
    #             print(f"Failed to fetch for {networks} {station} {otime}")
                continue

            _network = sta_inv[0].code
            slat = sta_inv[0][0].latitude
            slon = sta_inv[0][0].longitude
            olat = event.loc[event['idx']==idx, 'latitude'].values[0]
            olon = event.loc[event['idx']==idx, 'longitude'].values[0]

            dis1 = locations2degrees(olat, olon, slat, slon)
            dist = degrees2kilometers(dis1)
    #         if max_dist < dist:
    #             max_dist = dist

    #         if min_dist > dist:
    #             min_dist = dist

            distances.append([None, _network, station, dist])

        # Sort distances
        distances = sorted(distances, key=lambda item: item[-1])
        distances = distances[:idx_sta+1]

        # Set up to define the xlim and ylim
        max_y = 0
        min_y = 0
        # This count is for the if statements. Only used to ensure that min_y_count 
        #is changed from 0 to either the first positive value of the distance of one of the stations from the event
        min_y_count = 0 

        max_x = 0
        min_x = 0

        # This count is for the if statements. Only used to ensure that min_x_count 
        #is changed from 0 to either the first positive value of P pick time or the first positive value of S pick time
        min_x_count= 0
        # Create a figure
        fig,axs = plt.subplots(1,4,figsize=(18,6))
        gs = fig.add_gridspec(3, hspace=0, figure=fig)
    #     axs = gs.subplots(sharex=True, sharey=True)
        starttime = otime -30
        endtime = otime + 120

        # Define texts
        texts = []

        for i, ii in enumerate(distances):

            if ii[1] in ['NC', 'BK']:
                # Query waveforms
                st = client_ncedc.get_waveforms(network=ii[1], station=ii[2], location="*", channel=channel,starttime=starttime, endtime=endtime)

            elif ii[1] in networks: 
                st = client_waveform.get_waveforms(network=ii[1], station=ii[2], channel=channel,starttime=starttime, endtime=endtime)

            else: 
                st =  Stream()
                print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
                continue

    #         print(f"len(st):{len(st)}")
    #         print(st)

            # Skip empty traces
            if len(st) == 0:
                    continue

            sta_picks = picks_idx[picks_idx['station'] == ii[2]]
            p_picks = sta_picks.loc[sta_picks['phase'] == 'P']
            s_picks = sta_picks.loc[sta_picks['phase'] == 'S']
    #         print(len(p_picks),len(s_picks))

            # Define the xlim values
            # Define the maximum x value
            if len(s_picks) > 0:
                if max_x < UTCDateTime(s_picks.iloc[0]['time_pick']) - starttime:
                    max_x = UTCDateTime(s_picks.iloc[0]['time_pick']+5) - starttime
            elif len(p_picks) > 0:
                if max_x < UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime: 
                    max_x = UTCDateTime(p_picks.iloc[0]['time_pick']+5) - starttime
            else:
                print('No picks for this station. Skipping.')
                continue 

            # Define the minimum x value
            if len(p_picks) > 0:
                if min_x_count == 0:
                    if min_x < UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime:
                        min_x = UTCDateTime(p_picks.iloc[0]['time_pick']-5) - starttime
                        min_x_count += 1           
                else:
                    if min_x >= UTCDateTime(p_picks.iloc[0]['time_pick']) - starttime:
                        min_x = UTCDateTime(p_picks.iloc[0]['time_pick']-5) - starttime            
            elif len(s_picks) > 0:
                if min_x_count == 0:
                    if min_x < UTCDateTime(s_picks.iloc[0]['time_pick'])- starttime:
                        min_x = UTCDateTime(s_picks.iloc[0]['time_pick']-5)- starttime
                        min_x_count += 1                
                else:
                    if min_x >= UTCDateTime(s_picks.iloc[0]['time_pick'])- starttime:
                        min_x = UTCDateTime(s_picks.iloc[0]['time_pick']-5) - starttime
            else:
                print('No picks for this station. Skipping.')
                continue    

    #         if len(p_picks) == 0:
    #             continue

    #         print('This is after the p_pick continue statement')

            # Define ylim values
            if min_y_count == 0:
                if min_y < ii[3]:
                    min_y = ii[3] - 5
                    min_y_count += 1           
            else:
                if min_y >= ii[3]:
                    min_y = ii[3] - 5 

            max_y = ii[3] + 5

        scaling_factor = (1/2)*(max_y-min_y)   

        for i, ii in enumerate(distances):

            if ii[1] in ['NC', 'BK']:
                # Query waveforms
                st = client_ncedc.get_waveforms(network=ii[1], station=ii[2], location="*", channel=channel,starttime=starttime, endtime=endtime)

            elif ii[1] in networks: 
                st = client_waveform.get_waveforms(network=ii[1], station=ii[2], channel=channel,starttime=starttime, endtime=endtime)

            else: 
                st =  Stream()
                print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
                continue

    #         print(f"len(st):{len(st)}")
    #         print(st)

            # Skip empty traces
            if len(st) == 0:
                    continue
            _st = Stream()
            # Check for HH and BH channels presence
            has_HH = bool(st.select(channel="HH?"))
            has_BH = bool(st.select(channel="BH?"))

            # Apply selection logic based on channel presence
            if has_HH and has_BH:
                # If both HH and BH channels are present, select only HH
                _st += st.select(channel="HH?")
            elif has_HH:
                # If only HH channels are present
                _st += st.select(channel="HH?")
            elif has_BH:
                # If only BH channels are present
                _st += st.select(channel="BH?")

            st = _st

            print(f'Second st print:{_st}')

            st = Stream(filter(lambda st: st.stats.sampling_rate > 10, st))
            st.taper(max_percentage=0.05)
            st.filter(type='bandpass', freqmin=2, freqmax=25)
            st.merge(fill_value='interpolate') # fill gaps if there are any.

    #         print(st)
            # Select only one trace per channel
            unique_channels = set(tr.stats.channel for tr in st)
            selected_traces = []

            for ch in unique_channels:
                selected_traces.append(next(tr for tr in st if tr.stats.channel == ch))
            st = Stream(selected_traces)

            trim_st = st.copy()
            sta_picks = picks_idx[picks_idx['station'] == ii[2]]
            p_picks = sta_picks.loc[sta_picks['phase'] == 'P']
            s_picks = sta_picks.loc[sta_picks['phase'] == 'S']
    #         print(len(p_picks),len(s_picks))




    #         if len(p_picks) == 0:
    #             continue 
    #         print('This is after the p_pick continue statement')
            print(trim_st)

            for iax in range(len(trim_st)):
                print(iax)
                sampling_rate = trim_st[iax].stats.sampling_rate
                trim_st = trim_st.normalize()

                if len(p_picks)>0:
                    tp = UTCDateTime(p_picks.iloc[0]['time_pick']) - otime + 30
                    i1 = int((tp-5)*sampling_rate)
                    i2 = int((tp+15)*sampling_rate)
                elif len(s_picks)>0:
                    ts = UTCDateTime(s_picks.iloc[0]['time_pick']) - otime + 30
                    i1 = int((ts-10)*sampling_rate)
                    i2 = int((ts+10)*sampling_rate)
                else:
                    print(f"WARNING: No pick time for {ii[1]}.{ii[2]}.{channel} on {otime}.")

                offsets1 = ii[3]
                try: 
                    wave = trim_st[iax].data
                    wave = wave / (np.nanmax(wave[i1:i2], axis=-1)*10)
                except:
                    continue 

    #             print(trim_st[iax].stats.sampling_rate)
                axs[iax].plot(trim_st[iax].times(), wave * scaling_factor + offsets1, 
                              color='black', label=f"{trim_st[iax].stats.channel}", alpha=0.7, lw=0.5)
    #             axs[iax].plot(trim_st[iax].times(), wave * 30 + offsets1, color='black', label=f"{trim_st[iax].stats.channel}", alpha=0.7, lw=0.5)

    #             axs[iax].text(xlim[-1] + 2,   offsets1, 
    #                               [ii[2]], fontsize=8, verticalalignment='bottom')

                if len(p_picks) > 0:
                    axs[iax].vlines(UTCDateTime(p_picks.iloc[0]['time_pick']) - otime + 30, offsets1 - (1/35) * scaling_factor, 
                                    offsets1 + (1/35) * scaling_factor, color='r')
                if len(s_picks) > 0:
                    axs[iax].vlines(UTCDateTime(s_picks.iloc[0]['time_pick']) - otime + 30, offsets1 - (1/35) * scaling_factor, 
                                    offsets1 + (1/35) * scaling_factor, color='b')
            texts.append([ii[2],ii[3]])


    #     print(max_y,min_y)
        chs = ['2','1','Z']
        for iax in range(3):
            for i, ii in enumerate(texts):
                offsets1 = ii[1]
                axs[iax].text(max_x + 0.5, offsets1, 
                                      [ii[0]], fontsize=8, verticalalignment='bottom')
            axs[iax].legend(chs[iax],loc='upper right', handlelength=0)
            axs[iax].set_ylim([min_y,max_y])
            axs[iax].set_xlim([min_x,max_x])
            axs[iax].grid(alpha=0.5)
        fig.supxlabel('Time [sec]', y=0.07)
        fig.supylabel('Distance [km]')
        fig.suptitle(f"{title}: Origin Time={otime}, \n Latitude={round(event[event['idx']==idx]['latitude'].values[0], 2)}, Longtitude={round(event[event['idx']==idx]['longitude'].values[0], 2)}, Depth={round(event[event['idx']==idx]['depth'].values[0], 2)}", y=1)

        m = Basemap(projection='merc', llcrnrlat=40, urcrnrlat=50, llcrnrlon=-130, urcrnrlon=-120, resolution='i', ax=axs[3])
        m.drawcoastlines()
        m.drawcountries()
        m.drawstates()
        m.drawmapboundary()
        m.drawparallels(np.arange(40, 51, 1), labels=[1,0,0,0])
        m.drawmeridians(np.arange(-130, -119, 1), labels=[0,0,0,1])
        x, y = m(event[event['idx']==idx]['longitude'].values[0], event[event['idx']==idx]['latitude'].values[0])
        m.plot(x, y, 'ro', markersize=9)
        axs[3].set_title('Event Location')
        
        fig.savefig(p, format='pdf')  

    p.close()

### Specify the latitudes and longitudes

In [ ]:
new_events = pd.read_csv('../data/datasets_2014/new_events.csv')

In [ ]:
idx = new_events[new_events['station']=='J25B']['idx'].values
idx

In [ ]:
new_events = new_events[new_events["idx"].isin(idx)]
new_events

In [ ]:
new_events_specific_lat_lon = new_events.loc[(new_events['latitude']>46)&(new_events['latitude']<47.5)&(new_events['longitude']<-124)&(new_events['longitude']>-126)]
new_events_specific_lat_lon

In [ ]:
# new_events = new_events_specific_lat_lon.loc[(new_events_specific_lat_lon['depth']>1)&(new_events_specific_lat_lon['depth']<40)]
new_events = new_events_specific_lat_lon.loc[new_events_specific_lat_lon['picks']>=6][0:30]
new_events

### Histogram: Depths of events

In [ ]:
# Plot the histogram of the number of picks for the matched events
plt.figure()
bins = np.linspace(0,50,25)
plt.hist(new_events['depth'],bins=bins)
plt.xlabel('Depth (km)')
plt.ylabel('Number of Events')
plt.title('Histogram of the depths of the events in the cluster at ~46.5$^\circ$ N')

### Plot HH?

In [ ]:
# parameters
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "HH?"
idx_sta= 50
title= "Events matched"
fig_title= "events_matched.png"
ylim= [0,300]
xlim= [30,45]

for idx in new_events['idx']:
    subplots_cluster_scale_p(idx,mycatalog,mycatalog_picks,networks,channel,idx_sta,title,fig_title,ylim,xlim)

### Plot BH?

In [ ]:
# parameters
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "BH?"
idx_sta= 50
title= "Events matched"
fig_title= "events_matched.png"
ylim= [0,300]
xlim= [30,45]

for idx in new_events['idx']:
    subplots_cluster_scale_p(idx,mycatalog,mycatalog_picks,networks,channel,idx_sta,title,fig_title,ylim,xlim)

### Plot both HH? and BH?

In [ ]:
new_events['datetime'] = pd.to_datetime(new_events['datetime'], utc = True)
new_events

In [ ]:
# parameters for subplots_cluster_scale_p
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "?H?"
idx_sta= 50
title= "Events matched"
fig_title= "events_matched.png"

for idx in new_events['idx']:
    subplots_cluster_scale_p(idx,new_events,mycatalog_picks,networks,channel,idx_sta,title,fig_title)

In [ ]:
# parameters for subplots_cluster_scale
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "?H?"
idx_sta= 50
title= "Events matched"
fig_title= "new_events_plots.pdf"

subplots_cluster_scale(new_events,mycatalog_picks,networks,channel,idx_sta,title,fig_title)

In [ ]:
# Plot the histogram of the number of picks for the matched events
new_events['time'] = pd.to_datetime(new_events['time'])
year1 = 2012
time1 = datetime(year=year1, month=1, day=1)
time2 = datetime(year=year1 + 1, month=1, day=1)
time_bins = pd.date_range(start=time1, end=time2, freq='5D')
plt.figure()
plt.hist(new_events['time'], bins=time_bins)
plt.xlabel('Days')
plt.ylabel('Number of Events')
plt.title('Histogram for the frequency of the events in the cluster at ~46.5$^\circ$ N')
plt.xticks(rotation=45)  # Optional: Rotate x-axis labels for better readability
plt.show()

In [ ]:
import matplotlib 
from matplotlib import pyplot as plt 
from matplotlib.backends.backend_pdf import PdfPages 

# customizing runtime configuration stored 
# in matplotlib.rcParams 
plt.rcParams["figure.figsize"] = [7.00, 3.50] 
plt.rcParams["figure.autolayout"] = True

fig1 = plt.figure() 
plt.plot([17, 45, 7, 8, 7], color='orange') 

fig2 = plt.figure() 
plt.plot([13, 25, 1, 6, 3], color='blue') 

Fig3 = plt.figure() 
plt.plot([22, 11, 2, 1, 23], color='green') 


def save_image(filename): 
	
	# PdfPages is a wrapper around pdf 
	# file so there is no clash and create 
	# files with no error. 
	p = PdfPages(filename) 
	
	# get_fignums Return list of existing 
	# figure numbers 
	fig_nums = plt.get_fignums() 
	figs = [plt.figure(n) for n in fig_nums] 
	
	# iterating over the numbers in list 
	for fig in figs: 
		
		# and saving the files 
		fig.savefig(p, format='pdf') 
	
	# close the object 
	p.close() 

# name your Pdf file 
filename = "multi_plot_image.pdf"

# call the function 
save_image(filename) 


## Plot the cluster events at around 43.25&deg; N, 124.25&deg; W using the plotting functions 

In [ ]:
new_events_specific_lat_lon = unmatched_events_mycatalog2morton_and_anss.loc[(unmatched_events_mycatalog2morton_and_anss['latitude']>43.0)&(unmatched_events_mycatalog2morton_and_anss['latitude']<43.3)&(unmatched_events_mycatalog2morton_and_anss['longitude']<-124.25)&(unmatched_events_mycatalog2morton_and_anss['longitude']>-124.75)]
new_events_specific_lat_lon

In [ ]:
new_events = new_events_specific_lat_lon.loc[new_events_specific_lat_lon['picks']>5]
new_events

### Plot HH?

In [ ]:
# parameters
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "HH?"
idx_sta= 50
title= "Events matched"
fig_title= "events_matched.png"
ylim= [0,300]
xlim= [20,150]

for idx in new_events['idx']:
    subplots_cluster_scale_p(idx,mycatalog,mycatalog_picks,networks,channel,idx_sta,title,fig_title,ylim,xlim)

### Plot BH?

In [ ]:
# parameters
mycatalog= mycatalog
mycatalog_picks=mycatalog_picks
networks= all_picks_networks
channel= "BH?"
idx_sta= 50
title= "Events matched"
fig_title= "events_matched.png"
ylim= [0,300]
xlim= [20,150]

for idx in new_events['idx']:
    subplots_cluster_scale_p(idx,mycatalog,mycatalog_picks,networks,channel,idx_sta,title,fig_title,ylim,xlim)

## Calculate SNRs

In [ ]:
all_picks = pd.read_csv('../data/datasets_2014/all_picks_2014.csv')
all_pick_assignments = pd.read_csv('../data/datasets_2014/all_pick_assignments_2014.csv')

In [ ]:
def calc_snr(all_picks,all_pick_assignments):
    """ 
    This function calculates the SNRs for each station in each event.
    
    Inputs:
    1. The all_pick.csv file from the 2_format_pick2associate file.
    2. The all_pick_assignments.csv file from the 3_association file.
    
    Oututs:
    The new all_pick_assignments_snr file with the additional SNR column.
    """
    
    # Create the list of networks
    all_picks_networks = all_picks['station_network_code'].drop_duplicates()
    list_networks = list(all_picks_networks)
    networks = ','.join(all_picks_networks)
    
    
    
    # Define the clients 
    client_waveform = WaveformClient()
    client2 = Client("IRIS")
    client_ncedc = Client('NCEDC')
    
    all_pick_assignments['datetime'] = pd.to_datetime(all_pick_assignments['time'], utc = True)

    
    # Define parameters
    percentile=98
    
    # Create empty lists
    snr_list = []
        
    # Make sure if a station for an event has more than 1 P or S pick
    for idx in all_pick_assignments['idx'].drop_duplicates():
        # Define parameters
        otime = UTCDateTime(str(all_pick_assignments[all_pick_assignments['idx'] == idx]["datetime"].values[0]))


        # Create empty lists
        networks_stas = []

        # Plot the earthquake moveout for one of the unmatched events for all stations 
    #     event = mycatalog
        pick_idx = all_pick_assignments.loc[all_pick_assignments['idx']==idx]
        pick_sta = np.unique(pick_idx['station'])
        
    #     distances = []
    #     max_dist = 10
    #     min_dist = 0
        for station in pick_sta:

            sta_inv = client2.get_stations(network=networks,
                                           station=station, channel="?H?", 
                                           starttime=otime - 1e8, endtime=otime + 1e8,level="response")
            if len(sta_inv) == 0:
                print(f'No inventory for station {station}. Skipping.')
                continue

            network = sta_inv[0].code
    #         slat = sta_inv[0][0].latitude
    #         slon = sta_inv[0][0].longitude
    #         olat = event.loc[event['idx']==idx, 'latitude'].values[0]
    #         olon = event.loc[event['idx']==idx, 'longitude'].values[0]

    #         dis1 = locations2degrees(olat, olon, slat, slon)
    #         dist = degrees2kilometers(dis1)
    # #         if max_dist < dist:
    # #             max_dist = dist

    # #         if min_dist > dist:
    # #             min_dist = dist

            networks_stas.append([network,station])
        
   
        events = all_pick_assignments[all_pick_assignments['idx']==idx]
        for i in networks_stas:
            events1 = events[events['station']==i[1]]
            p_picks = events1[events1['phase']=='P']
            s_picks = events1[events1['phase']=='S']
            

            if len(p_picks)>0 and len(s_picks)>0:
                print(p_picks['datetime'].values,s_picks['datetime'].values)
                p_pick_time = UTCDateTime(str(p_picks['datetime'].values[0]))
                s_pick_time = UTCDateTime(str(s_picks['datetime'].values[0]))
                
                starttime_st = UTCDateTime(p_pick_time)-timedelta(seconds=120)
                endtime_st = UTCDateTime(p_pick_time)+timedelta(seconds=120)
                
                starttime_noise = UTCDateTime(p_pick_time)-timedelta(seconds=8)
                endtime_noise = UTCDateTime(p_pick_time)
                
                starttime_signal = UTCDateTime(s_pick_time)-timedelta(seconds=1)
                endtime_signal = UTCDateTime(s_pick_time)+timedelta(seconds=2)
                
                print(starttime_noise,endtime_noise)
            
                if i[0] in ['NC', 'BK']:
                # Query waveforms
                    st = client_ncedc.get_waveforms(network=i[0], station=i[1],
                                                    location="*", channel="?HZ",starttime=starttime_st,
                                                    endtime=endtime_st)

                elif i[0] in networks: 
                    st = client_waveform.get_waveforms(network=i[0], station=i[1],
                                                       channel='?HZ',starttime=starttime_st, endtime=endtime_st)

                else: 
                    st =  Stream()
                    print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
                    continue

        #         print(f"len(st):{len(st)}")
        #         print(st)

                # Skip empty traces
                if len(st) == 0:
                    continue
                    
                print(f'First st print:{st}')
                # Create a new stream
                _st = Stream()
                # Check for HH and BH channels presence
                has_HH = bool(st.select(channel="HH?"))
                has_BH = bool(st.select(channel="BH?"))

                # Apply selection logic based on channel presence
                if has_HH and has_BH:
                    # If both HH and BH channels are present, select only HH
                    _st += st.select(channel="HH?")
                elif has_HH:
                    # If only HH channels are present
                    _st += st.select(channel="HH?")
                elif has_BH:
                    # If only BH channels are present
                    _st += st.select(channel="BH?")

                _st.merge(fill_value='interpolate') # fill gaps if there are any.

                print(f'Second st print:{_st}')
            
                noise = _st.copy().trim(starttime=starttime_noise,endtime=endtime_noise)    
                signal = _st.copy().trim(starttime=starttime_signal,endtime=endtime_signal) 
                
                print(f"P and S pick times:{p_pick_time} and {s_pick_time}")
                print(f"Stream start and end times:{starttime_st} and {endtime_st}")
                print(f"Noise start and end times:{starttime_noise} and {endtime_noise}")
                print(f"Signal start and end times:{starttime_signal} and {endtime_signal}")
                
                print(f'Noise:{noise}')
                print(f'Signal:{signal}')

                noise_abs = np.percentile(abs(noise[0].data),percentile)
                signal_abs = np.percentile(abs(signal[0].data),percentile)

                snr = 20 * np.log10((signal_abs/noise_abs))

                snr_list.append(snr)
                
            if len(p_picks)>0 and len(s_picks)==0:
                
                print(p_picks['datetime'].values,s_picks['datetime'].values)
                p_pick_time = UTCDateTime(str(p_picks['datetime'].values[0]))
#                 s_pick_time = UTCDateTime(str(s_picks['datetime'].values[0]))

                starttime_st = UTCDateTime(p_pick_time)-timedelta(seconds=120)
                endtime_st = UTCDateTime(p_pick_time)+timedelta(seconds=120)
                
                starttime_noise = UTCDateTime(p_pick_time)-timedelta(seconds=8)
                endtime_noise = UTCDateTime(p_pick_time)
                
                starttime_signal = UTCDateTime(p_pick_time)+timedelta(seconds=1)
                endtime_signal = UTCDateTime(p_pick_time)+timedelta(seconds=4)
                
            
                if i[0] in ['NC', 'BK']:
                # Query waveforms
                    st = client_ncedc.get_waveforms(network=i[0], station=i[1],
                                                    location="*", channel="?HZ",starttime=starttime_st, 
                                                    endtime=endtime_st)

                elif i[0] in networks: 
                    st = client_waveform.get_waveforms(network=i[0], station=i[1],
                                                       channel='?HZ',starttime=starttime_st, endtime=endtime_st)

                else: 
                    st =  Stream()
                    print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
                    continue

        #         print(f"len(st):{len(st)}")
        #         print(st)

                # Skip empty traces
                if len(st) == 0:
                    continue
                print(f'First st print:{st}')
                # Create a new stream
                _st = Stream()
                # Check for HH and BH channels presence
                has_HH = bool(st.select(channel="HH?"))
                has_BH = bool(st.select(channel="BH?"))

                # Apply selection logic based on channel presence
                if has_HH and has_BH:
                    # If both HH and BH channels are present, select only HH
                    _st += st.select(channel="HH?")
                elif has_HH:
                    # If only HH channels are present
                    _st += st.select(channel="HH?")
                elif has_BH:
                    # If only BH channels are present
                    _st += st.select(channel="BH?")

                _st.merge(fill_value='interpolate') # fill gaps if there are any.

                print(f'Second st print:{_st}')
                
                
                    

                noise = _st.copy().trim(starttime=starttime_noise,endtime=endtime_noise)    
                signal = _st.copy().trim(starttime=starttime_signal,endtime=endtime_signal) 
                
                print(f"P pick time:{p_pick_time}")
                print(f"Stream start and end times:{starttime_st} and {endtime_st}")
                print(f"Noise start and end times:{starttime_noise} and {endtime_noise}")
                print(f"Signal start and end times:{starttime_signal} and {endtime_signal}")

                print(f'Noise:{noise}')
                print(f'Signal:{signal}')

                noise_abs = np.percentile(abs(noise[0].data),percentile)
                signal_abs = np.percentile(abs(signal[0].data),percentile)

                snr = 20 * np.log10((signal_abs/noise_abs))

                snr_list.append(snr)
                    
            if len(p_picks)==0 and len(s_picks)>0:
                print(p_picks['datetime'].values,s_picks['datetime'].values)
#                 p_pick_time = UTCDateTime(str(p_picks['datetime'].values))
                s_pick_time = UTCDateTime(str(s_picks['datetime'].values[0]))
    
                starttime_st = UTCDateTime(s_pick_time)-timedelta(seconds=120)
                endtime_st = UTCDateTime(s_pick_time)+timedelta(seconds=120)
                
                starttime_noise = UTCDateTime(s_pick_time)-timedelta(seconds=8)
                endtime_noise = UTCDateTime(s_pick_time)
                
                starttime_signal = UTCDateTime(s_pick_time)
                endtime_signal = UTCDateTime(s_pick_time)+timedelta(seconds=3)
                
                print(starttime_noise,endtime_noise)
            
                if i[0] in ['NC', 'BK']:
                # Query waveforms
                    st = client_ncedc.get_waveforms(network=i[0], station=i[1],
                                                    location="*", channel="?HZ",starttime=starttime_st, 
                                                    endtime=endtime_st)

                elif i[0] in networks: 
                    st = client_waveform.get_waveforms(network=i[0], station=i[1],
                                                       channel='?HZ',starttime=starttime_st, endtime=endtime_st)

                else: 
                    st =  Stream()
                    print(f"WARNING: No data for {ii[1]}.{ii[2]}.{channel} on {otime}.")    
                    continue

        #         print(f"len(st):{len(st)}")
        #         print(st)

                # Skip empty traces
                if len(st) == 0:
                    continue
                    
                print(f'First st print:{st}')
                # Create a new stream
                _st = Stream()
                # Check for HH and BH channels presence
                has_HH = bool(st.select(channel="HH?"))
                has_BH = bool(st.select(channel="BH?"))

                # Apply selection logic based on channel presence
                if has_HH and has_BH:
                    # If both HH and BH channels are present, select only HH
                    _st += st.select(channel="HH?")
                elif has_HH:
                    # If only HH channels are present
                    _st += st.select(channel="HH?")
                elif has_BH:
                    # If only BH channels are present
                    _st += st.select(channel="BH?")

                _st.merge(fill_value='interpolate') # fill gaps if there are any.

                print(f'Second st print:{_st}')

            
                noise = _st.copy().trim(starttime=starttime_noise,endtime=endtime_noise)    
                signal = _st.copy().trim(starttime=starttime_signal,endtime=endtime_signal) 
                
                print(f"S pick time:{s_pick_time}")
                print(f"Stream start and end times:{starttime_st} and {endtime_st}")
                print(f"Noise start and end times:{starttime_noise} and {endtime_noise}")
                print(f"Signal start and end times:{starttime_signal} and {endtime_signal}")
                
                print(f'Noise:{noise}')
                print(f'Signal:{signal}')

                noise_abs = np.percentile(abs(noise[0].data),percentile)
                signal_abs = np.percentile(abs(signal[0].data),percentile)

                snr = 20 * np.log10((signal_abs/noise_abs))

                snr_list.append(snr)
            
    all_assignments_picks['snr']=snr_list
     
    return snr_list

In [ ]:
snr_list = calc_snr(all_picks,all_pick_assignments)

In [ ]:
snr_list

In [ ]:
client_waveform = WaveformClient()

p_pick_time = '2014-01-02T07:40:02.642533Z'

starttime_st = UTCDateTime(p_pick_time)-timedelta(seconds=120)
endtime_st = UTCDateTime(p_pick_time)+timedelta(seconds=120)

# starttime_st = UTCDateTime('2011-01-03T00:00:0.000000Z')
# endtime_st = UTCDateTime('2011-01-03T12:59:59.000000Z')

print(f'Requested start and end times:{starttime_st} and {endtime_st}')


st = client_waveform.get_waveforms(network='CN', station='BTB',
                                       channel='HHZ',starttime=starttime_st, endtime=endtime_st)
print(f'Actual start and end times: {st[0].stats.starttime} and {st[0].stats.endtime}')
